# Lesson 7: `groupby` and Indexing

## Objectives

`pandas` is a very popular library used by data scientists to process **tabular data**: data organized into rows and columns like a spreadsheet. In this lesson, we'll discuss two key `DataFrame` operations: the `groupby` operation and the `apply` operation. We'll also discuss how `groupby` introduces an extra level of complexity towards indexing and slicing values. By the end of this lesson, students will be able to:

* Explain in plain English the outcome of a `pandas` `DataFrame` `groupby` operation.
* Apply the `groupby` operation to a `pandas` `DataFrame`.
* Apply the `apply` operation to a `pandas` `DataFrame`.
* Select values from a hierarchical index using tuples and the `slice` object as keys.


## `groupby`

Last time, we computed the "shakiness" of each location as the sum of all the magnitudes of earthquakes in that location across all time. For instructional purposes, let's review how to compute shakiness without `pandas` (using a list of dictionaries) and with `pandas` (using a `DataFrame`).

### Processing a List of Dictionaries
For this problem, we want to process the `earthquakes.csv` as a list of dictionaries and return the result as a dictionary (where the keys are place names and the values are ShakeFactor).

In [23]:
import cse163_utils

In [24]:
# Using the code we wrote to parse the CSV to a list of dictionaries
data = cse163_utils.parse('earthquakes.csv')
data[:5]  # First 5 rows-- food for thought: how would we get the first five rows from a DataFrame?

[{'id': 'nc72666881',
  'year': 2016,
  'month': 7,
  'day': 27,
  'latitude': 37.6723333,
  'longitude': -121.619,
  'name': 'California',
  'magnitude': 1.43},
 {'id': 'us20006i0y',
  'year': 2016,
  'month': 7,
  'day': 27,
  'latitude': 21.5146,
  'longitude': 94.5721,
  'name': 'Burma',
  'magnitude': 4.9},
 {'id': 'nc72666891',
  'year': 2016,
  'month': 7,
  'day': 27,
  'latitude': 37.5765,
  'longitude': -118.85916670000002,
  'name': 'California',
  'magnitude': 0.06},
 {'id': 'nc72666896',
  'year': 2016,
  'month': 7,
  'day': 27,
  'latitude': 37.5958333,
  'longitude': -118.99483329999998,
  'name': 'California',
  'magnitude': 0.4},
 {'id': 'nn00553447',
  'year': 2016,
  'month': 7,
  'day': 27,
  'latitude': 39.3775,
  'longitude': -119.845,
  'name': 'Nevada',
  'magnitude': 0.3}]

To compute shakiness, we'll follow these steps:

* Create a result dictionary
* For each earthquake, find its `name` and `magnitude` and add the `magnitude` to the corresponding `name`.
 

In [25]:
shakiness = {}  # Empty dictionary
for earthquake in data:
    name = earthquake['name']
    magnitude = earthquake['magnitude']
    shakiness[name] += magnitude

shakiness

KeyError: 'California'

Uh-oh! We get a `KeyError` because we are trying to set values of a dictionary before we've initialized any keys! When using a `dict` as a counter, remember that we have to check for the key before trying to modify its value. Let's try again.

In [ ]:
shakiness = {}  # Empty dictionary
for earthquake in data:
    name = earthquake['name']
    magnitude = earthquake['magnitude']
    if name not in shakiness:
        shakiness[name] = 0
    shakiness[name] += magnitude

shakiness

{'California': 3638.4900000000084,
 'Burma': 22.200000000000003,
 'Nevada': 496.6400000000006,
 'Alaska': 3407.0000000000005,
 'Hawaii': 375.2099999999998,
 'Montana': 91.19000000000001,
 'Puerto Rico': 385.99999999999983,
 'Chile': 157.79999999999998,
 'Dominican Republic': 97.70000000000002,
 'British Virgin Islands': 230.09999999999994,
 'Indonesia': 298.60000000000014,
 'Washington': 176.2199999999999,
 'Southern East Pacific Rise': 15.799999999999999,
 'Argentina': 49.3,
 'Philippines': 85.19999999999999,
 'Canada': 99.96,
 'Papua New Guinea': 130.3,
 'Afghanistan': 43.6,
 'Oregon': 107.23000000000002,
 'South of Africa': 4.5,
 'Peru': 63.800000000000004,
 'Fiji': 75.0,
 'Japan': 192.60000000000002,
 'Oklahoma': 192.79999999999993,
 'Mexico': 111.45,
 'Kyrgyzstan': 39.8,
 'Tennessee': 36.24,
 'Tonga': 66.5,
 'Arkansas': 6.66,
 'South of the Fiji Islands': 77.00000000000001,
 'Utah': 71.59,
 'Georgia': 4.2,
 'U.S. Virgin Islands': 84.49999999999999,
 'Idaho': 27.930000000000003,
 '

And then we are done! It looks like California is the shakiest place on Earth!

What we have just done is a **group by** operation on the data. We put all the earthquakes into groups *by* some column label such as `name`, *selected* column values of interest such as `magnitude`, and *aggregated* (by summing with `+`) the values in each group.



### Processing a `pandas` `DataFrame`
Since group by is such a common operation, `pandas` has its own syntax. Understanding how the list of dictionaries approach works is a good starting point to understand what happens in the background when using `pandas`.

In [ ]:
import pandas as pd

In [ ]:
df = pd.read_csv('earthquakes.csv')
df

id  year  month  day   latitude   longitude        name  \
0     nc72666881  2016      7   27  37.672333 -121.619000  California   
1     us20006i0y  2016      7   27  21.514600   94.572100       Burma   
2     nc72666891  2016      7   27  37.576500 -118.859167  California   
3     nc72666896  2016      7   27  37.595833 -118.994833  California   
4     nn00553447  2016      7   27  39.377500 -119.845000      Nevada   
...          ...   ...    ...  ...        ...         ...         ...   
8389  nc72685246  2016      8   25  36.515499 -121.099831  California   
8390  ak13879193  2016      8   25  61.498400 -149.862700      Alaska   
8391  nc72685251  2016      8   25  38.805000 -122.821503  California   
8392  ci37672328  2016      8   25  34.308000 -118.635333  California   
8393  ci37672360  2016      8   25  34.119167 -116.933667  California   

      magnitude  
0          1.43  
1          4.90  
2          0.06  
3          0.40  
4          0.30  
...         ...  
8389       2.42  
8390       1.40  
8391       1.06  
8392       1.55  
8393       0.89  

[8394 rows x 8 columns]

We first show how to do this in pandas, and then we will go back and explain what the syntax is saying.

In [ ]:
df.groupby('name')['magnitude'].sum()

name
Afghanistan                         43.60
Alaska                            3407.00
Anguilla                             2.40
Argentina                           49.30
Arizona                              4.39
                                   ...   
Washington                         176.22
West Virginia                        2.31
Western Indian-Antarctic Ridge       4.50
Western Xizang                       9.40
Wyoming                             46.30
Name: magnitude, Length: 118, dtype: float64

The way to read this line of code uses the following logic:
* `df` is the `DataFrame` we want to process
* `.groupby('name')` tells the `DataFrame` we want it to group all of its rows **`by`** the `name` attribute. Conceptually, this step splits all the data into groups by `name`.
* **For each group**, `['magnitude'].sum()` selects the `magnitude` from all rows in that group and aggregates the data by taking the `sum` of the rows.

We can substitute `sum` aggregation operation for any other `Series` methods like `min`, `max`, and `mean`. You can also group by any column or use any column for your computations!

The final result is a `Series` that uses the `name` as its index. Remember that most of the datasets we've seen had integer indices, but we noted that his was not always the case. The result of a groupby has the values you used for group (in this case the string names of locations) as the indices. This makes it convenient to find the shakiness of California specifically, for example.

In [ ]:
shakiness = df.groupby('name')['magnitude'].sum()
shakiness['California']

3638.4900000000084

### What's going on here?
It's pretty incredible that such a short line of code can do something so complex. In the bullet-list above, I described the steps that happen here but I find it easier to think about it with a small example. The figure below shows a visual explanation of what is going on when you do a `groupby`.

1. **Teal, `data`**. Specify the `DataFrame`.
2. **Purple, `.groupby('col1')`**. Call the `groupby` function on that `DataFrame` passing `col1` as the column for forming groups. This splits the data up into groups based on the provided column.
    * This calls the `DataFrame.groupby(...)` method, **not** indexing with `[]`! Note the parentheses rather than square brackets.
3. **Red, `['col2'].sum()`**. Specify the aggregation column, `col2`, and the aggregation function, `.sum()`. The values in each group are aggregated into a single value.
    * This selects a particular column by indexing with `[]`.
4. **Green, `result = `**. The final result evaluates to a `Series` with `col1` as the index and the aggregation value for each group.

![Groupby Diagram, as explained by the numbered list above](groupby.png)

To get better understand what's going on, let's freeze at step 3 (before aggregating results into a `Series`) to see how Pandas represents the `groupby` operation.

In [ ]:
# Make a DataFrame by giving it a list of dictionaries
example_data = pd.DataFrame([
    {'col1': 'A', 'col2': 1},
    {'col1': 'B', 'col2': 2},
    {'col1': 'C', 'col2': 3},
    {'col1': 'A', 'col2': 4},
    {'col1': 'C', 'col2': 5},
])

example_data

col1  col2
0    A     1
1    B     2
2    C     3
3    A     4
4    C     5

In [ ]:
groupby = example_data.groupby('col1') # Notice no aggregate
groupby

This returns a special `pandas` object called a `DataFrameGroupBy`. This represents an "unfinished" `groupby` operation since we have not computed an aggregate yet. One feature that is kind of helpful for seeing what's going on (but you will probably rarely use in practice) is the fact you can loop over a `DataFrameGroupBy` to inspect the groups.

In [ ]:
for key, group in groupby: 
    display(group) # To get the fancy Jupyter Notebook display of table

col1  col2
0    A     1
3    A     4

col1  col2
1    B     2

col1  col2
2    C     3
4    C     5

Alternatively, you can use the `.describe()` function, which gives several different summary statistics.

In [ ]:
groupby['col2'].describe()

count  mean       std  min   25%  50%   75%  max
col1                                                  
A       2.0   2.5  2.121320  1.0  1.75  2.5  3.25  4.0
B       1.0   2.0       NaN  2.0  2.00  2.0  2.00  2.0
C       2.0   4.0  1.414214  3.0  3.50  4.0  4.50  5.0

This is why when we do finish the computation, we get the sum of all these rows that fell into each group

In [ ]:
result = example_data.groupby('col1')['col2'].sum()
result

col1
A    5
B    2
C    8
Name: col2, dtype: int64

It's important to highlight that **`result` is a `Series` with the step 2 group-by names as its index**. You can access the underlying `index` of a `Series` or `DataFrame` using its `.index` attribute.

In [ ]:
print(type(result))
print(result.index)
print(result['C'])

<class 'pandas.core.series.Series'>
Index(['A', 'B', 'C'], dtype='object', name='col1')
8


### When to use this?
Whenever you want to separate your data into groups to get some value for each one, this is the natural time to ues a `groupby`! Whenever you see "for each" or "per" in a question, it's likely you will want to use a `groupby`. 

Here are some example questions you can solve with a groupby. We provide some "code" to compute each one, assuming the data had columns with the relevant names.
* Compute the number of students per section
    ```
    grades.groupby('Section')['StudentID'].count()
    ```
* Compute the average grade of students in each section
    ```
    grades.groupby('Section')['Grade'].mean()
    ```
* Compute the total number of people in each country
    ```
    cities.groupby('country')['population'].sum()
    ```

**Food for thought:** What would happen if we wanted to use `groupby` with multiple columns? For example:

In [ ]:
df.groupby(['year', 'month', 'day'])['magnitude'].describe()

count      mean       std   min     25%    50%     75%   max
year month day                                                              
2016 7     27   272.0  1.617574  1.095349  0.06  0.9000  1.400  2.0000  5.60
           28   308.0  1.448149  0.896851  0.10  0.8775  1.240  1.8000  5.10
           29   309.0  1.640129  1.165952  0.01  0.8800  1.450  1.9000  7.70
           30   329.0  1.615076  1.262618  0.03  0.7000  1.240  2.0000  5.70
           31   278.0  1.750827  1.261577  0.10  0.9000  1.500  2.1475  5.90
     8     1    356.0  1.520056  1.157326  0.04  0.8000  1.245  1.8025  6.10
           2    292.0  1.539418  1.089946  0.05  0.8000  1.300  1.9000  5.50
           3    294.0  1.556327  1.147365  0.01  0.8300  1.200  1.8150  5.10
           4    420.0  1.249190  1.034738  0.05  0.6000  1.000  1.5825  6.30
           5    256.0  1.428789  1.144244  0.10  0.6200  1.185  1.7150  5.70
           6    316.0  1.313228  1.065587  0.09  0.5600  1.100  1.6200  5.40
           7    316.0  1.356994  1.078556  0.10  0.6000  1.120  1.7425  5.10
           8    335.0  1.484925  1.131495  0.02  0.6300  1.200  1.9900  5.10
           9    272.0  1.614779  1.164186  0.10  0.8075  1.300  1.9000  5.09
           10   329.0  1.404742  1.038701  0.02  0.7700  1.170  1.7400  5.40
           11   356.0  1.390534  1.159147  0.04  0.6775  1.100  1.7000  7.20
           12   326.0  1.533282  1.158696  0.04  0.7400  1.200  1.9000  5.40
           13   284.0  1.421901  1.080338  0.10  0.7000  1.105  1.7775  5.20
           14   231.0  1.692684  1.372191  0.05  0.8200  1.200  1.9000  5.90
           15   222.0  1.583964  1.157553  0.07  0.8550  1.300  1.8400  5.40
           16   223.0  1.629910  1.223131  0.10  0.7300  1.300  2.0000  5.10
           17   220.0  1.583682  1.203617  0.10  0.8000  1.210  1.9675  5.20
           18   219.0  1.499772  1.159497  0.04  0.7600  1.200  1.8050  5.90
           19   226.0  1.819469  1.416291  0.11  0.8925  1.340  2.1900  7.40
           20   237.0  1.553207  1.296262  0.02  0.7000  1.200  2.0000  6.40
           21   266.0  1.332368  1.032210  0.03  0.6050  1.140  1.6925  5.10
           22   215.0  1.451488  1.185657  0.01  0.7000  1.180  1.8000  5.60
           23   233.0  1.643391  1.245661  0.04  0.8200  1.300  2.1000  6.20
           24   216.0  1.553194  1.144054  0.03  0.8375  1.290  1.9000  6.80
           25   238.0  1.519328  0.926028  0.10  0.8900  1.400  1.9950  5.90

## `apply`

Earlier, we saw how arithmetic operators like `+`, `-`, `*`, and `/` apply element-wise to `pandas` `DataFrames` or `Series`.


In [ ]:
df['magnitude'] * 2

What if we wanted to find the length of each value in the name column? You might try something like the following and hope it does an element-wise computation as well.

In [ ]:
len(df['name'])

This is evaluating to the number of elements in the entire `Series`, not the length of each place `name`! Only certain operators support element-wise computation.
* Arithmetic operators such as `+`, `-`, `*`, `/`, etc.
* Comparison operators such as `==`, `<`, etc.
* Logical operators such as `&`, `|`, `~`.

Other functions will act on the entire `Series`, just as we saw with `len`!

### Built-in Functions on `pandas`
To call the `len` function on each `str`, use the magic syntax below.

In [ ]:
df['name'].str.len()

This reads, "Take the name column, apply the `len` function defined for `str`s to each element in the `Series`." The syntax looks unusual at first, but it helps programmers be clear about the data type and the function to apply to each element! We won't look at other data types now but there is a similar syntax for those as well.

Now you aren't limited to just calling `len` here, you can call pretty much any `str` function using this syntax.

* `str.lower()` to lower-case each string and return them as a new `Series`.
* `str.upper()` to upper-case each string and return them as a new `Series`.
* `str.len()` to compute the length of each string and return them as a new `Series`.
* `str.strip()`, `str.lstrip()`, `str.rstrip()` to trim whitespace from each string and return them as a new `Series`.

For example, the following cell shows how to convert each name to its upper-case version.

In [ ]:
df['name'].str.upper()

Note that this operation does not modify the original name column but rather returns a new `Series` with all the names upper-cased.

What if you wanted to write your own function to transform a value and apply it to each element in a `Series`? For example, what if I wanted to grab the first two characters from each name? 

This is where we will need the more general `apply` function defined for `pandas` objects. `apply` is more general than using the specific `str` functions we saw above since it will let you call your own functions on each element. Before we show how to do the specific example of grabbing the first two characters from the names, let's use this new approach to find the `len` of each name.

In [ ]:
df['name'].apply(len)

The first part, `df['name'].apply(`, should probably make some sense to you. We are calling some function named `apply` on the `Series` `df['name']`. What's very strange about this is it seems to be passing `len` **as a parameter** to the `apply` function! `len` is not being called directly here but passed as a parameter so that it can be later applied to each element.

This is probably the first time that you've seen this syntax. While this does look very strange, this is a feature of Python. A function is, in some sense, just like any other value in Python. But unlike `int`, `str`, or `list`, a Python function doesn't represent data (like numbers, strings, or collections of such data). A Python function represents an algorithm that can later be applied to some data!

So the authors of `pandas` who wrote the `apply` function, wrote it to take a parameter that is **another function** like `len`. They then call that function on each element in the `Series`. As Python programmers, we can write our own functions that take other functions as parameters too.

In [ ]:
def list_apply(values, function):
    """
    Takes a list of values and a function, and applies that function
    to each value in values. The given function must take one parameter
    as input and the returned list will be the result of calling that
    function once for each value in the list.
    """
    # It's not necessary to use a list comprehension here, 
    # but it's the easiest way to write this method!
    return [function(v) for v in values]

list_apply(['I', 'love', 'dogs'], len)

There is no restriction to only passing in the `len` function as a parameter here. You can pass any function that takes a single argument.

So if we write a function `first_two` that takes a `str` and returns the first two characters, then we can pass `first_two` to `apply`.

In [ ]:
def first_two(s):
    """
    Returns the first two characters of the given str as a str.
    
    Assumes there are at least two characters in s.
    """
    return s[:2]

df['name'].apply(first_two)

**Food for thought:** What happens to the parameter in the function definition? What if we had multiple parameters?

### Saving Results
Remember this `apply` function doesn't modify any data in the `DataFrame` or `Series`, but rather returns a new one. It's common that you want to save the result of an `apply` to your dataset to use those values later. Just like how you can use the `[]` assignment syntax for `list` and `dict` types in Python, we can also assign columns directly to a `pandas` `DataFrame`.

We can use this syntax to update an existing column.

In [ ]:
df['name'] = df['name'].str.upper()
df

Or use it to introduce a new column to the `DataFrame`.

In [ ]:
df['first_two_letters'] = df['name'].apply(first_two)
df

## Hierarchical indexing

Let's revisit `groupby` to take note of something interesting. Take a look at the indices that result from the following `groupby` call:

In [28]:
magnitudes = df.groupby(['year', 'month', 'day'])['magnitude'].describe()
magnitudes

count      mean       std   min     25%    50%     75%   max
year month day                                                              
2016 7     27   272.0  1.617574  1.095349  0.06  0.9000  1.400  2.0000  5.60
           28   308.0  1.448149  0.896851  0.10  0.8775  1.240  1.8000  5.10
           29   309.0  1.640129  1.165952  0.01  0.8800  1.450  1.9000  7.70
           30   329.0  1.615076  1.262618  0.03  0.7000  1.240  2.0000  5.70
           31   278.0  1.750827  1.261577  0.10  0.9000  1.500  2.1475  5.90
     8     1    356.0  1.520056  1.157326  0.04  0.8000  1.245  1.8025  6.10
           2    292.0  1.539418  1.089946  0.05  0.8000  1.300  1.9000  5.50
           3    294.0  1.556327  1.147365  0.01  0.8300  1.200  1.8150  5.10
           4    420.0  1.249190  1.034738  0.05  0.6000  1.000  1.5825  6.30
           5    256.0  1.428789  1.144244  0.10  0.6200  1.185  1.7150  5.70
           6    316.0  1.313228  1.065587  0.09  0.5600  1.100  1.6200  5.40
           7    316.0  1.356994  1.078556  0.10  0.6000  1.120  1.7425  5.10
           8    335.0  1.484925  1.131495  0.02  0.6300  1.200  1.9900  5.10
           9    272.0  1.614779  1.164186  0.10  0.8075  1.300  1.9000  5.09
           10   329.0  1.404742  1.038701  0.02  0.7700  1.170  1.7400  5.40
           11   356.0  1.390534  1.159147  0.04  0.6775  1.100  1.7000  7.20
           12   326.0  1.533282  1.158696  0.04  0.7400  1.200  1.9000  5.40
           13   284.0  1.421901  1.080338  0.10  0.7000  1.105  1.7775  5.20
           14   231.0  1.692684  1.372191  0.05  0.8200  1.200  1.9000  5.90
           15   222.0  1.583964  1.157553  0.07  0.8550  1.300  1.8400  5.40
           16   223.0  1.629910  1.223131  0.10  0.7300  1.300  2.0000  5.10
           17   220.0  1.583682  1.203617  0.10  0.8000  1.210  1.9675  5.20
           18   219.0  1.499772  1.159497  0.04  0.7600  1.200  1.8050  5.90
           19   226.0  1.819469  1.416291  0.11  0.8925  1.340  2.1900  7.40
           20   237.0  1.553207  1.296262  0.02  0.7000  1.200  2.0000  6.40
           21   266.0  1.332368  1.032210  0.03  0.6050  1.140  1.6925  5.10
           22   215.0  1.451488  1.185657  0.01  0.7000  1.180  1.8000  5.60
           23   233.0  1.643391  1.245661  0.04  0.8200  1.300  2.1000  6.20
           24   216.0  1.553194  1.144054  0.03  0.8375  1.290  1.9000  6.80
           25   238.0  1.519328  0.926028  0.10  0.8900  1.400  1.9950  5.90

In `pandas`, a `DataFrame` can have a **hierarchical index** (or, a multi-level index) called a `MultiIndex`. We can use the `.index` property to investigate this further.

In [29]:
magnitudes.index

MultiIndex([(2016, 7, 27),
            (2016, 7, 28),
            (2016, 7, 29),
            (2016, 7, 30),
            (2016, 7, 31),
            (2016, 8,  1),
            (2016, 8,  2),
            (2016, 8,  3),
            (2016, 8,  4),
            (2016, 8,  5),
            (2016, 8,  6),
            (2016, 8,  7),
            (2016, 8,  8),
            (2016, 8,  9),
            (2016, 8, 10),
            (2016, 8, 11),
            (2016, 8, 12),
            (2016, 8, 13),
            (2016, 8, 14),
            (2016, 8, 15),
            (2016, 8, 16),
            (2016, 8, 17),
            (2016, 8, 18),
            (2016, 8, 19),
            (2016, 8, 20),
            (2016, 8, 21),
            (2016, 8, 22),
            (2016, 8, 23),
            (2016, 8, 24),
            (2016, 8, 25)],
           names=['year', 'month', 'day'])

**Food for thought:** See a familiar data structure?

The `MultiIndex` comes in handy when your data might have multiple categorical dimensions. It allows us to work with and manipulate data with multiple levels as though it were one. Some common use cases are:

* Time-series data with multiple columns for time units (like the year, month, and day in `earthquakes.csv`)
* Experimental data with multiple factors that are difficult to represent in two dimensions
* Geographical data with nested location columns (such as country, state, city)
* Grouping data on multiple dimensions (hence why we see it with multi-column `groupby`!)

### Indexing a `MultiIndex`

We can use `.loc` with `MultiIndex`, but the syntax will look a bit strange. Recall that `.loc[]` takes in a row indexer and a column indexer, like so:

```python
df.loc[row_indexer, column_indexer]
```

To select a specific combination of values in the `MultiIndex`, you would need to use a `tuple`.

In [31]:
magnitudes.loc[(2016, 8, 7), :]

count    316.000000
mean       1.356994
std        1.078556
min        0.100000
25%        0.600000
50%        1.120000
75%        1.742500
max        5.100000
Name: (2016, 8, 7), dtype: float64

Even though there are three values in the `MultiIndex`, we don't need to select all of them! In the following slice, we have:

* The `'year'` index set to `2016`
* The `'month'` index set to `8`

Notice that we didn't specify a `'day'` index, so we still see all the possible `'day'` values that have a `'year'` of `2016` and a `'month'` of `8`.

In [32]:
magnitudes.loc[(2016, 8), :]

count      mean       std   min     25%    50%     75%   max
day                                                              
1    356.0  1.520056  1.157326  0.04  0.8000  1.245  1.8025  6.10
2    292.0  1.539418  1.089946  0.05  0.8000  1.300  1.9000  5.50
3    294.0  1.556327  1.147365  0.01  0.8300  1.200  1.8150  5.10
4    420.0  1.249190  1.034738  0.05  0.6000  1.000  1.5825  6.30
5    256.0  1.428789  1.144244  0.10  0.6200  1.185  1.7150  5.70
6    316.0  1.313228  1.065587  0.09  0.5600  1.100  1.6200  5.40
7    316.0  1.356994  1.078556  0.10  0.6000  1.120  1.7425  5.10
8    335.0  1.484925  1.131495  0.02  0.6300  1.200  1.9900  5.10
9    272.0  1.614779  1.164186  0.10  0.8075  1.300  1.9000  5.09
10   329.0  1.404742  1.038701  0.02  0.7700  1.170  1.7400  5.40
11   356.0  1.390534  1.159147  0.04  0.6775  1.100  1.7000  7.20
12   326.0  1.533282  1.158696  0.04  0.7400  1.200  1.9000  5.40
13   284.0  1.421901  1.080338  0.10  0.7000  1.105  1.7775  5.20
14   231.0  1.692684  1.372191  0.05  0.8200  1.200  1.9000  5.90
15   222.0  1.583964  1.157553  0.07  0.8550  1.300  1.8400  5.40
16   223.0  1.629910  1.223131  0.10  0.7300  1.300  2.0000  5.10
17   220.0  1.583682  1.203617  0.10  0.8000  1.210  1.9675  5.20
18   219.0  1.499772  1.159497  0.04  0.7600  1.200  1.8050  5.90
19   226.0  1.819469  1.416291  0.11  0.8925  1.340  2.1900  7.40
20   237.0  1.553207  1.296262  0.02  0.7000  1.200  2.0000  6.40
21   266.0  1.332368  1.032210  0.03  0.6050  1.140  1.6925  5.10
22   215.0  1.451488  1.185657  0.01  0.7000  1.180  1.8000  5.60
23   233.0  1.643391  1.245661  0.04  0.8200  1.300  2.1000  6.20
24   216.0  1.553194  1.144054  0.03  0.8375  1.290  1.9000  6.80
25   238.0  1.519328  0.926028  0.10  0.8900  1.400  1.9950  5.90

We can use `slice(None)` to select all values at a particular level. So, if we wanted all the values in August (when `'month'` is `8`) and it didn't matter what day or year it was, we might do the following:

In [45]:
magnitudes.loc[(slice(None), 8, slice(None)), :]

count      mean       std   min     25%    50%     75%   max
year month day                                                              
2016 8     1    356.0  1.520056  1.157326  0.04  0.8000  1.245  1.8025  6.10
           2    292.0  1.539418  1.089946  0.05  0.8000  1.300  1.9000  5.50
           3    294.0  1.556327  1.147365  0.01  0.8300  1.200  1.8150  5.10
           4    420.0  1.249190  1.034738  0.05  0.6000  1.000  1.5825  6.30
           5    256.0  1.428789  1.144244  0.10  0.6200  1.185  1.7150  5.70
           6    316.0  1.313228  1.065587  0.09  0.5600  1.100  1.6200  5.40
           7    316.0  1.356994  1.078556  0.10  0.6000  1.120  1.7425  5.10
           8    335.0  1.484925  1.131495  0.02  0.6300  1.200  1.9900  5.10
           9    272.0  1.614779  1.164186  0.10  0.8075  1.300  1.9000  5.09
           10   329.0  1.404742  1.038701  0.02  0.7700  1.170  1.7400  5.40
           11   356.0  1.390534  1.159147  0.04  0.6775  1.100  1.7000  7.20
           12   326.0  1.533282  1.158696  0.04  0.7400  1.200  1.9000  5.40
           13   284.0  1.421901  1.080338  0.10  0.7000  1.105  1.7775  5.20
           14   231.0  1.692684  1.372191  0.05  0.8200  1.200  1.9000  5.90
           15   222.0  1.583964  1.157553  0.07  0.8550  1.300  1.8400  5.40
           16   223.0  1.629910  1.223131  0.10  0.7300  1.300  2.0000  5.10
           17   220.0  1.583682  1.203617  0.10  0.8000  1.210  1.9675  5.20
           18   219.0  1.499772  1.159497  0.04  0.7600  1.200  1.8050  5.90
           19   226.0  1.819469  1.416291  0.11  0.8925  1.340  2.1900  7.40
           20   237.0  1.553207  1.296262  0.02  0.7000  1.200  2.0000  6.40
           21   266.0  1.332368  1.032210  0.03  0.6050  1.140  1.6925  5.10
           22   215.0  1.451488  1.185657  0.01  0.7000  1.180  1.8000  5.60
           23   233.0  1.643391  1.245661  0.04  0.8200  1.300  2.1000  6.20
           24   216.0  1.553194  1.144054  0.03  0.8375  1.290  1.9000  6.80
           25   238.0  1.519328  0.926028  0.10  0.8900  1.400  1.9950  5.90

### Resetting Indices

The `.reset_index()` method converts index levels back into regular columns. This is useful when you need to perform column-wise operations or when you want to "flatten" your data structure.

By default, `.reset_index()` moves all index levels to their own columns and assigns integer indices starting from 0:

In [46]:
magnitudes_reset = magnitudes.reset_index()
magnitudes_reset

year  month  day  count      mean       std   min     25%    50%     75%  \
0   2016      7   27  272.0  1.617574  1.095349  0.06  0.9000  1.400  2.0000   
1   2016      7   28  308.0  1.448149  0.896851  0.10  0.8775  1.240  1.8000   
2   2016      7   29  309.0  1.640129  1.165952  0.01  0.8800  1.450  1.9000   
3   2016      7   30  329.0  1.615076  1.262618  0.03  0.7000  1.240  2.0000   
4   2016      7   31  278.0  1.750827  1.261577  0.10  0.9000  1.500  2.1475   
5   2016      8    1  356.0  1.520056  1.157326  0.04  0.8000  1.245  1.8025   
6   2016      8    2  292.0  1.539418  1.089946  0.05  0.8000  1.300  1.9000   
7   2016      8    3  294.0  1.556327  1.147365  0.01  0.8300  1.200  1.8150   
8   2016      8    4  420.0  1.249190  1.034738  0.05  0.6000  1.000  1.5825   
9   2016      8    5  256.0  1.428789  1.144244  0.10  0.6200  1.185  1.7150   
10  2016      8    6  316.0  1.313228  1.065587  0.09  0.5600  1.100  1.6200   
11  2016      8    7  316.0  1.356994  1.078556  0.10  0.6000  1.120  1.7425   
12  2016      8    8  335.0  1.484925  1.131495  0.02  0.6300  1.200  1.9900   
13  2016      8    9  272.0  1.614779  1.164186  0.10  0.8075  1.300  1.9000   
14  2016      8   10  329.0  1.404742  1.038701  0.02  0.7700  1.170  1.7400   
15  2016      8   11  356.0  1.390534  1.159147  0.04  0.6775  1.100  1.7000   
16  2016      8   12  326.0  1.533282  1.158696  0.04  0.7400  1.200  1.9000   
17  2016      8   13  284.0  1.421901  1.080338  0.10  0.7000  1.105  1.7775   
18  2016      8   14  231.0  1.692684  1.372191  0.05  0.8200  1.200  1.9000   
19  2016      8   15  222.0  1.583964  1.157553  0.07  0.8550  1.300  1.8400   
20  2016      8   16  223.0  1.629910  1.223131  0.10  0.7300  1.300  2.0000   
21  2016      8   17  220.0  1.583682  1.203617  0.10  0.8000  1.210  1.9675   
22  2016      8   18  219.0  1.499772  1.159497  0.04  0.7600  1.200  1.8050   
23  2016      8   19  226.0  1.819469  1.416291  0.11  0.8925  1.340  2.1900   
24  2016      8   20  237.0  1.553207  1.296262  0.02  0.7000  1.200  2.0000   
25  2016      8   21  266.0  1.332368  1.032210  0.03  0.6050  1.140  1.6925   
26  2016      8   22  215.0  1.451488  1.185657  0.01  0.7000  1.180  1.8000   
27  2016      8   23  233.0  1.643391  1.245661  0.04  0.8200  1.300  2.1000   
28  2016      8   24  216.0  1.553194  1.144054  0.03  0.8375  1.290  1.9000   
29  2016      8   25  238.0  1.519328  0.926028  0.10  0.8900  1.400  1.9950   

     max  
0   5.60  
1   5.10  
2   7.70  
3   5.70  
4   5.90  
5   6.10  
6   5.50  
7   5.10  
8   6.30  
9   5.70  
10  5.40  
11  5.10  
12  5.10  
13  5.09  
14  5.40  
15  7.20  
16  5.40  
17  5.20  
18  5.90  
19  5.40  
20  5.10  
21  5.20  
22  5.90  
23  7.40  
24  6.40  
25  5.10  
26  5.60  
27  6.20  
28  6.80  
29  5.90

You could optionally pass in the name of an index level to turn it into a column instead. Take a look at the following:

In [48]:
magnitudes_year_reset = magnitudes.reset_index(level="year")
magnitudes_year_reset

year  count      mean       std   min     25%    50%     75%   max
month day                                                                    
7     27   2016  272.0  1.617574  1.095349  0.06  0.9000  1.400  2.0000  5.60
      28   2016  308.0  1.448149  0.896851  0.10  0.8775  1.240  1.8000  5.10
      29   2016  309.0  1.640129  1.165952  0.01  0.8800  1.450  1.9000  7.70
      30   2016  329.0  1.615076  1.262618  0.03  0.7000  1.240  2.0000  5.70
      31   2016  278.0  1.750827  1.261577  0.10  0.9000  1.500  2.1475  5.90
8     1    2016  356.0  1.520056  1.157326  0.04  0.8000  1.245  1.8025  6.10
      2    2016  292.0  1.539418  1.089946  0.05  0.8000  1.300  1.9000  5.50
      3    2016  294.0  1.556327  1.147365  0.01  0.8300  1.200  1.8150  5.10
      4    2016  420.0  1.249190  1.034738  0.05  0.6000  1.000  1.5825  6.30
      5    2016  256.0  1.428789  1.144244  0.10  0.6200  1.185  1.7150  5.70
      6    2016  316.0  1.313228  1.065587  0.09  0.5600  1.100  1.6200  5.40
      7    2016  316.0  1.356994  1.078556  0.10  0.6000  1.120  1.7425  5.10
      8    2016  335.0  1.484925  1.131495  0.02  0.6300  1.200  1.9900  5.10
      9    2016  272.0  1.614779  1.164186  0.10  0.8075  1.300  1.9000  5.09
      10   2016  329.0  1.404742  1.038701  0.02  0.7700  1.170  1.7400  5.40
      11   2016  356.0  1.390534  1.159147  0.04  0.6775  1.100  1.7000  7.20
      12   2016  326.0  1.533282  1.158696  0.04  0.7400  1.200  1.9000  5.40
      13   2016  284.0  1.421901  1.080338  0.10  0.7000  1.105  1.7775  5.20
      14   2016  231.0  1.692684  1.372191  0.05  0.8200  1.200  1.9000  5.90
      15   2016  222.0  1.583964  1.157553  0.07  0.8550  1.300  1.8400  5.40
      16   2016  223.0  1.629910  1.223131  0.10  0.7300  1.300  2.0000  5.10
      17   2016  220.0  1.583682  1.203617  0.10  0.8000  1.210  1.9675  5.20
      18   2016  219.0  1.499772  1.159497  0.04  0.7600  1.200  1.8050  5.90
      19   2016  226.0  1.819469  1.416291  0.11  0.8925  1.340  2.1900  7.40
      20   2016  237.0  1.553207  1.296262  0.02  0.7000  1.200  2.0000  6.40
      21   2016  266.0  1.332368  1.032210  0.03  0.6050  1.140  1.6925  5.10
      22   2016  215.0  1.451488  1.185657  0.01  0.7000  1.180  1.8000  5.60
      23   2016  233.0  1.643391  1.245661  0.04  0.8200  1.300  2.1000  6.20
      24   2016  216.0  1.553194  1.144054  0.03  0.8375  1.290  1.9000  6.80
      25   2016  238.0  1.519328  0.926028  0.10  0.8900  1.400  1.9950  5.90

In [49]:
magnitudes_day_year_reset = magnitudes.reset_index(level=["year", "day"])
magnitudes_day_year_reset

year  day  count      mean       std   min     25%    50%     75%   max
month                                                                         
7      2016   27  272.0  1.617574  1.095349  0.06  0.9000  1.400  2.0000  5.60
7      2016   28  308.0  1.448149  0.896851  0.10  0.8775  1.240  1.8000  5.10
7      2016   29  309.0  1.640129  1.165952  0.01  0.8800  1.450  1.9000  7.70
7      2016   30  329.0  1.615076  1.262618  0.03  0.7000  1.240  2.0000  5.70
7      2016   31  278.0  1.750827  1.261577  0.10  0.9000  1.500  2.1475  5.90
8      2016    1  356.0  1.520056  1.157326  0.04  0.8000  1.245  1.8025  6.10
8      2016    2  292.0  1.539418  1.089946  0.05  0.8000  1.300  1.9000  5.50
8      2016    3  294.0  1.556327  1.147365  0.01  0.8300  1.200  1.8150  5.10
8      2016    4  420.0  1.249190  1.034738  0.05  0.6000  1.000  1.5825  6.30
8      2016    5  256.0  1.428789  1.144244  0.10  0.6200  1.185  1.7150  5.70
8      2016    6  316.0  1.313228  1.065587  0.09  0.5600  1.100  1.6200  5.40
8      2016    7  316.0  1.356994  1.078556  0.10  0.6000  1.120  1.7425  5.10
8      2016    8  335.0  1.484925  1.131495  0.02  0.6300  1.200  1.9900  5.10
8      2016    9  272.0  1.614779  1.164186  0.10  0.8075  1.300  1.9000  5.09
8      2016   10  329.0  1.404742  1.038701  0.02  0.7700  1.170  1.7400  5.40
8      2016   11  356.0  1.390534  1.159147  0.04  0.6775  1.100  1.7000  7.20
8      2016   12  326.0  1.533282  1.158696  0.04  0.7400  1.200  1.9000  5.40
8      2016   13  284.0  1.421901  1.080338  0.10  0.7000  1.105  1.7775  5.20
8      2016   14  231.0  1.692684  1.372191  0.05  0.8200  1.200  1.9000  5.90
8      2016   15  222.0  1.583964  1.157553  0.07  0.8550  1.300  1.8400  5.40
8      2016   16  223.0  1.629910  1.223131  0.10  0.7300  1.300  2.0000  5.10
8      2016   17  220.0  1.583682  1.203617  0.10  0.8000  1.210  1.9675  5.20
8      2016   18  219.0  1.499772  1.159497  0.04  0.7600  1.200  1.8050  5.90
8      2016   19  226.0  1.819469  1.416291  0.11  0.8925  1.340  2.1900  7.40
8      2016   20  237.0  1.553207  1.296262  0.02  0.7000  1.200  2.0000  6.40
8      2016   21  266.0  1.332368  1.032210  0.03  0.6050  1.140  1.6925  5.10
8      2016   22  215.0  1.451488  1.185657  0.01  0.7000  1.180  1.8000  5.60
8      2016   23  233.0  1.643391  1.245661  0.04  0.8200  1.300  2.1000  6.20
8      2016   24  216.0  1.553194  1.144054  0.03  0.8375  1.290  1.9000  6.80
8      2016   25  238.0  1.519328  0.926028  0.10  0.8900  1.400  1.9950  5.90

**Food for thought:** When might it be preferable to use a `MultiIndex`? When might it not be preferable?

## ⏸️ Pause and 🧠 Think

Take a moment to review the following concepts and reflect on your own understanding. A good temperature check for your understanding is asking yourself whether you might be able to explain these concepts to a friend outside of this class.

Here's what we covered in this lesson:

* `groupby`
* `apply`
* Hierarchical indexing and `MultiIndex`

Here are some other guiding exercises and questions to help you reflect on what you've seen so far:

1. In your own words, write a few sentences summarizing what you learned in this lesson.
2. What did you find challenging in this lesson? Come up with some questions you might ask your peers or the course staff to help you better understand that concept.
3. What was familiar about what you saw in this lesson? How might you relate it to things you have learned before?
4. Throughout the lesson, there were a few **Food for thought** questions. Try exploring one or more of them and see what you find.

## In-Class

When you come to class, we will work together on the problems in `ufos.ipynb`. We will also need `ufos.csv` for these tasks. Make sure that you have a way of editing and running these files!

## Canvas Quiz

All done with the lesson? Complete the [<u>Canvas Quiz linked here!</u>](https://canvas.uw.edu/courses/1860345/quizzes/2334842)
